In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 26,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
163 181 2018-04-02 2018   2     25     GE        HW        117       
164 182 2018-04-01 2018   2     25     SY        PA         71       
165 183 2018-04-01 2018   2     25     WB        WC         70       
166 184 2018-03-31 2018   2     25     FR        ES        106       
167 185 2018-03-31 2018   2     25     BL        ME         74       
168 186 2018-03-31 2018   2     25     CW        GW         79       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
163 118        18         ... 1.840                1.925               
164  94        10         ... 1.854                1.925               
165 121         9         ... 1.813                2.200               
166  90        16         ... 1.877                1.925               
167 100        10         ... 1.925                1.925               
168  95        12         ... 1.925                1.925               
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
163 1.840                  1.925                  1.925                
164 1.892                  1.925                  1.925                
165 1.934                  1.925                  1.925                
166 1.877                  1.925                  1.925                
167 1.925                  1.925                  1.925                
168 2.000                  1.925                  1.854                
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
163 2.020                 2.020                          1          16         
164 1.961                 1.961                         17          13         
165 1.925                 1.917                          4           8         
166 1.990                 1.980                          9          18         
167 1.925                 1.925                          7           5         
168 1.925                 1.854                          3          10

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 26,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
154 172 2018-04-08 2018   3     26     WC        GE         95       
155 173 2018-04-08 2018   3     26     WB        ES        104       
156 174 2018-04-08 2018   3     26     RI        HW        102       
157 175 2018-04-07 2018   3     26     SK        AD         55       
158 176 2018-04-07 2018   3     26     SY        GW        103       
159 177 2018-04-07 2018   3     26     GC        FR         68       
160 178 2018-04-07 2018   3     26     ME        NM        123       
161 179 2018-04-07 2018   3     26     PA        BL         97       
162 180 2018-04-06 2018   3     26     CA        CW         76       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
154  80        14         ... 1.9                  1.9                 
155  83        14         ... 1.9                  1.9                 
156  89        15         ... 1.9                  1.9                 
157 104         7         ... 1.9                  1.9                 
158  87        16         ... 1.9                  1.9                 
159  96        10         ... 1.9                  1.9                 
160  86        18         ... 1.9                  1.9                 
161  92        14         ... 1.9                  1.9                 
162 100        11         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
154 1.9                    1.9                    1.9                  
155 1.9                    1.9                    1.9                  
156 1.9                    1.9                    1.9                  
157 1.9                    1.9                    1.9                  
158 1.9                    1.9                    1.9                  
159 1.9                    1.9                    1.9                  
160 1.9                    1.9                    1.9                  
161 1.9                    1.9                    1.9                  
162 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
154 1.9                   1.9                           17           9         
155 1.9                   1.9                           16           6         
156 1.9                   1.9                            8          14         
157 1.9                   1.9                            2           7         
158 1.9                   1.9                            5           1         
159 1.9                   1.9                           18           3         
160 1.9                   1.9                           11          15         
161 1.9                   1.9                           10          12         
162 1.9                   1.9                           13           4

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [12]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd    2.5%    25%    50%    75%
delta                      0.67    0.00   0.07    0.53   0.62   0.68   0.72
attackGoals_raw[1,1]       1.95    0.09   2.58   -3.19   0.28   1.99   3.74
attackGoals_raw[1,2]      -4.82    0.09   2.85   -8.95  -7.14  -5.14  -2.91
attackGoals_raw[1,3]      -3.38    0.11   3.24   -8.72  -5.94  -3.56  -1.04
attackGoals_raw[1,4]      -0.13    0.12   3.03   -6.40  -2.18   0.04   1.96
attackGoals_raw[1,5]       0.57    0.08   2.56   -4.26  -1.14   0.59   2.26
attackGoals_raw[1,6]       0.94    0.09   2.76   -4.63  -0.91   1.10   2.92
attackGoals_raw[1,7]      -0.18    0.09   2.45   -4.80  -1.90  -0.24   1.49
attackGoals_raw[1,8]       1.42    0.09   2.69   -3.93  -0.36   1.42   3.23
attackGoals_raw[1,9]       1.35    0.06   1.85   -2.19

In [11]:
fit <- sflist2stanfit(sflist)

In [12]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     8.748217e-01 1.181555e-03 6.935465e-02  7.353555e-01
attackGoals_raw[1,1]      1.849178e+00 6.619783e-02 2.534771e+00 -3.157912e+00
attackGoals_raw[1,2]     -1.555524e+00 6.537622e-02 3.226911e+00 -7.634004e+00
attackGoals_raw[1,3]      1.392384e+00 6.208097e-02 2.865496e+00 -4.328930e+00
attackGoals_raw[1,4]     -2.164350e+00 6.107171e-02 2.785353e+00 -7.300940e+00
attackGoals_raw[1,5]      1.192982e+00 5.826604e-02 3.127149e+00 -5.160915e+00
attackGoals_raw[1,6]      9.980334e-01 6.280183e-02 2.915508e+00 -4.705272e+00
attackGoals_raw[1,7]      1.205087e+00 5.729555e-02 2.805848e+00 -4.290198e+00
attackGoals_raw[1,8]      2.810419e-02 5.158039e-02 2.693566e+00 -5.189915e+00
attackGoals_raw[1,9]      6.202097e-02 6.906187e-02 3.095002e+00 -5.958713e+00
attackGoals_raw[1,10]    -3.194097e+00 5.532112e-02 3.287422e+00 -8.593086e+00
attackGoals_raw[1,11]     1.823946e+00 6.46

# Extract parameters

In [13]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [14]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [15]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [16]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [17]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [18]:
actual.total.diff
correct.vec

[1]  15  21  13 -49  16 -28  37   5 -24

[1]  TRUE  TRUE  TRUE FALSE  TRUE FALSE FALSE  TRUE FALSE

# Calculate percentage of win, loss and draw

In [19]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [20]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.4658 0.5724 0.8662 0.9388 0.9052 0.8212 0.3062 0.8872 0.9574
      [2,] 0.0438 0.0312 0.0158 0.0076 0.0310 0.0290 0.0478 0.0132 0.0086
      [3,] 0.4904 0.3964 0.1180 0.0536 0.0638 0.1498 0.6460 0.0996 0.0340

In [21]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [22]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [23]:
sim.pred.mat

[,1]                [,2]    [,3]    [,4]     [,5]     [,6]    [,7]   
 [1,] behind diff         -1.6908 19.539  2.101    6.7538   8.187   19.591 
 [2,] goal diff           0.783   -1.9614 24.1832  45.5984  13.5866 6.2578 
 [3,] total diff          3.0072  7.7706  147.2002 280.3442 89.7066 57.1378
 [4,] home team           WC      WB      RI       SK       SY      GC     
 [5,] away team           GE      ES      HW       AD       GW      FR     
 [6,] actual result       15      21      13       -49      16      -28    
 [7,] prediction correct? TRUE    TRUE    TRUE     FALSE    TRUE    FALSE  
 [8,] home win prob       0.4658  0.5724  0.8662   0.9388   0.9052  0.8212 
 [9,] draw prob           0.0438  0.0312  0.0158   0.0076   0.031   0.029  
[10,] home loss prob      0.4904  0.3964  0.118    0.0536   0.0638  0.1498 
[11,] simulated sd ests   78.98   92.48   389.81   739.6    183.77  144    
      [,8]     [,9]    [,10]   
 [1,] 1.8472   5.5926  9.7174  
 [2,] -3.0586  24.8464 42.777  
 [3,] -16.5044 154.671 266.3794
 [4,] ME       PA      CA      
 [5,] NM       BL      CW      
 [6,] 37       5       -24     
 [7,] FALSE    TRUE    FALSE   
 [8,] 0.3062   0.8872  0.9574  
 [9,] 0.0478   0.0132  0.0086  
[10,] 0.646    0.0996  0.034   
[11,] 75.33    339.32  546.98

In [24]:
write.csv(t(sim.pred.mat),  file = "round3_prediction.csv")